# Biodiversity Metrics — Hands-on Practice

Follow this guided lab to reproduce the workflow presented in the *Biodiversity metrics & metabarcoding* lecture. Each exercise mirrors a concept from the slides so that you can redo the analyses step by step. Work in order, execute your own solution in the placeholder cell, and reveal the provided answer only after you tried.

**How to use this notebook**

- Run the notebook with an R kernel.
- Complete each code task in the `# your work here` cell.
- Compare with the hidden solution when you are confident in your attempt.
- Keep notes about questions or observations so that we can review them during lab time.

## Series 1 – Preparing the Environment
Focus: installing and loading every package used throughout the lecture (devtools, tidyverse, vegan, latex2exp, kableExtra, MetabarSchool).

### Exercise 1.1 – Install the required packages

Install *devtools*, *tidyverse*, *vegan*, *latex2exp*, and *kableExtra* from CRAN if they are not already available. Then install **MetabarSchool** from the Git repository shown in the lecture.

In [ ]:
# your work here

In [ ]:
# Solution
if (!requireNamespace('devtools', quietly = TRUE)) install.packages('devtools', dependencies = TRUE)
if (!requireNamespace('tidyverse', quietly = TRUE)) install.packages('tidyverse', dependencies = TRUE)
if (!requireNamespace('vegan', quietly = TRUE)) install.packages('vegan', dependencies = TRUE)
if (!requireNamespace('latex2exp', quietly = TRUE)) install.packages('latex2exp', dependencies = TRUE)
if (!requireNamespace('kableExtra', quietly = TRUE)) install.packages('kableExtra', dependencies = TRUE)
if (!requireNamespace('MetabarSchool', quietly = TRUE)) {
  devtools::install_git('https://git.metabarcoding.org/MetabarcodingSchool/biodiversity-metrics.git')
}

### Exercise 1.2 – Load every library

Attach tidyverse, vegan, latex2exp, kableExtra, and MetabarSchool so that their functions are available for the rest of the notebook.

In [ ]:
# your work here

In [ ]:
# Solution
library(tidyverse)
library(vegan)
library(latex2exp)
library(kableExtra)
library(MetabarSchool)

## Series 2 – Exploring the mock community dataset
Focus: loading the `positive.*` objects that describe the mock community and understanding their structure.

### Exercise 2.1 – Load the mock community data

Load `positive.count`, `positive.samples`, and `positive.motus` from the MetabarSchool package.

In [ ]:
# your work here

In [ ]:
# Solution
data('positive.count')
data('positive.samples')
data('positive.motus')

### Exercise 2.2 – Inspect matrices and metadata

Display the dimensions of `positive.count`, the first rows of `positive.samples`, and the first rows of `positive.motus` to replicate the introductory slides.

In [ ]:
# your work here

In [ ]:
# Solution
dim(positive.count)
head(positive.samples, n = 3)
head(positive.motus, n = 3)

## Series 3 – Early data curation
Focus: removing singleton MOTUs and visualizing the uneven sequencing depth highlighted in the lecture.

### Exercise 3.1 – Remove singleton MOTUs

Count how many MOTUs occur once across the full dataset and filter them out of both `positive.count` and `positive.motus`.

In [ ]:
# your work here

In [ ]:
# Solution
singleton.mask <- colSums(positive.count) > 1
table(singleton.mask)
positive.count <- positive.count[, singleton.mask]
positive.motus <- positive.motus[singleton.mask, ]

### Exercise 3.2 – Examine read depth per PCR

Plot the distribution of total reads per PCR (log scale optional) to confirm that sequencing depth is heterogeneous.

In [ ]:
# your work here

In [ ]:
# Solution
par(bg = NA)
hist(rowSums(positive.count), breaks = 15,
     xlab = 'Read counts', main = 'Number of reads per PCR')

### Exercise 3.3 – Test the influence of dilution

Reproduce the boxplot of read counts across dilution levels and compute the ANOVA that quantifies the fraction of variance explained by dilution.

In [ ]:
# your work here

In [ ]:
# Solution
par(bg = NA)
boxplot(rowSums(positive.count) ~ positive.samples$dilution, log = 'y',
        xlab = 'Dilution', ylab = 'Total reads')
aov_table <- summary(aov(rowSums(positive.count) ~ positive.samples$dilution))[[1]]
round((aov_table['positive.samples$dilution', 'Sum Sq'] / sum(aov_table[, 'Sum Sq'])) * 100, 1)

## Series 4 – Rarefaction workflow
Focus: rarefying all PCRs to the same depth and documenting which MOTUs are retained.

### Exercise 4.1 – Rarefy down to 2,000 reads

Find the minimum sequencing depth across PCRs and run `rrarefy()` so that every PCR contains exactly 2,000 reads.

In [ ]:
# your work here

In [ ]:
# Solution
min_reads <- min(rowSums(positive.count))
min_reads
positive.count.rarefied <- rrarefy(positive.count, sample = 2000)

### Exercise 4.2 – Track retained MOTUs

Identify which MOTUs have non-zero counts after rarefaction. Keep those columns in the rarefied count matrix as well as in `positive.motus`.

In [ ]:
# your work here

In [ ]:
# Solution
are.still.present <- colSums(positive.count.rarefied) > 0
table(are.still.present)
positive.count.rarefied <- positive.count.rarefied[, are.still.present]
positive.motus.rare <- positive.motus[are.still.present, ]

### Exercise 4.3 – Compare distributions before and after

Use histograms or boxplots to compare the MOTU read-count distribution before and after rarefaction, as shown on the slides.

In [ ]:
# your work here

In [ ]:
# Solution
par(mfrow = c(1, 2), bg = NA)
hist(log10(colSums(positive.count) + 1), breaks = 30,
     xlab = expression(log[10](reads~per~MOTU)), main = 'Not rarefied',
     xlim = c(0, 6), ylim = c(0, 2300))
hist(log10(colSums(positive.count.rarefied) + 1), breaks = 30,
     xlab = expression(log[10](reads~per~MOTU)), main = 'Rarefied data',
     xlim = c(0, 6), ylim = c(0, 2300))

## Series 5 – Relative frequencies
Focus: transforming counts to relative abundances so that all PCRs sum to one.

### Exercise 5.1 – Compute relative frequencies

Apply `decostand(..., method = "total")` to convert the raw `positive.count` matrix into `positive.count.relfreq`.

In [ ]:
# your work here

In [ ]:
# Solution
positive.count.relfreq <- decostand(positive.count, method = 'total')

### Exercise 5.2 – Check for empty MOTUs

Verify that no MOTU sums to zero after the relative-frequency transformation.

In [ ]:
# your work here

In [ ]:
# Solution
table(colSums(positive.count.relfreq) == 0)

## Series 6 – Alpha-diversity on toy environments
Focus: rehearse richness, Gini–Simpson, Shannon entropy, and Hill numbers exactly as on the lecture example.

### Exercise 6.1 – Encode the two environments and compute richness

Create the two probability vectors from the slides (E1 and E2), bind them into a matrix named `environments`, and compute richness `S` for each.

In [ ]:
# your work here

In [ ]:
# Solution
E1 <- c(A = 0.25, B = 0.25, C = 0.25, D = 0.25, E = 0, F = 0, G = 0)
E2 <- c(A = 0.55, B = 0.07, C = 0.02, D = 0.17, E = 0.07, F = 0.07, G = 0.03)
environments <- rbind(`Environment 1` = E1, `Environment 2` = E2)
S <- rowSums(environments > 0)
S

### Exercise 6.2 – Compute Gini–Simpson and Shannon indices

Use the formulas from the slides to compute Gini–Simpson (`1 - sum(p^2)`) and Shannon entropy (`-sum(p * log(p))`) for each environment.

In [ ]:
# your work here

In [ ]:
# Solution
GiniSimpson <- 1 - rowSums(environments^2)
Shannon <- -rowSums(environments * log(environments), na.rm = TRUE)
data.frame(`Gini-Simpson` = GiniSimpson, `Shannon` = Shannon)

### Exercise 6.3 – Convert Shannon entropy to Hill numbers

Follow the lecture by transforming Shannon entropy to Hill numbers via `exp(H)`.

In [ ]:
# your work here

In [ ]:
# Solution
Hill <- exp(-rowSums(environments * log(environments), na.rm = TRUE))
Hill

## Series 7 – Generalized entropy and biodiversity spectra
Focus: implementing the `log_q`, `exp_q`, `H_q`, and `D_q` helpers and generating diversity spectra just like on the slides.

### Exercise 7.1 – Implement the generalized log and exponential

Write the `log_q()` and `exp_q()` functions introduced in the lecture. They should fall back to the natural log/exp when `q = 1`.

In [ ]:
# your work here

In [ ]:
# Solution
log_q <- function(x, q = 1) {
  if (q == 1) {
    log(x)
  } else {
    (x^(1 - q) - 1) / (1 - q)
  }
}
exp_q <- function(x, q = 1) {
  if (q == 1) {
    exp(x)
  } else {
    (1 + (1 - q) * x)^(1 / (1 - q))
  }
}

### Exercise 7.2 – Build entropy and diversity spectra

Define `H_q()`, `D_q()`, `H_spectrum()`, and `D_spectrum()`, then compute the spectra for the toy environments over `q = seq(0, 3, by = 0.1)`.

In [ ]:
# your work here

In [ ]:
# Solution
H_q <- function(x, q = 1) {
  sum(x * log_q(1 / x, q), na.rm = TRUE)
}
D_q <- function(x, q = 1) {
  exp_q(H_q(x, q), q)
}
H_spectrum <- function(x, q = 1) {
  sapply(q, function(Q) H_q(x, Q))
}
D_spectrum <- function(x, q = 1) {
  sapply(q, function(Q) D_q(x, Q))
}
qs <- seq(0, 3, by = 0.1)
environments.H <- apply(environments, MARGIN = 1, H_spectrum, q = qs)
environments.D <- apply(environments, MARGIN = 1, D_spectrum, q = qs)
list(H = environments.H, D = environments.D)

### Exercise 7.3 – Compare spectra for the mock community

Use the `plants.16` dataset and the mock-community relative frequencies to compute `H.mock`, `D.mock`, and the distributions of `positive.H` and `positive.D` shown on the slides.

In [ ]:
# your work here

In [ ]:
# Solution
data('plants.16')
positive.count.relfreq <- decostand(positive.count, method = 'total')
H.mock <- H_spectrum(plants.16$dilution, q = qs)
D.mock <- D_spectrum(plants.16$dilution, q = qs)
positive.H <- apply(positive.count.relfreq, MARGIN = 1, H_spectrum, q = qs)
positive.D <- apply(positive.count.relfreq, MARGIN = 1, D_spectrum, q = qs)
list(H.mock = H.mock, D.mock = D.mock, positive.H = positive.H, positive.D = positive.D)

## Series 8 – Impact of extra cleaning on α-diversity
Focus: repeating the spectral computation on the cleaned dataset (`positive.clean.count`).

### Exercise 8.1 – Load the cleaned counts and normalize

Load `positive.clean.count`, convert it to relative frequencies, and store the result in `positive.clean.count.relfreq`.

In [ ]:
# your work here

In [ ]:
# Solution
data('positive.clean.count')
positive.clean.count.relfreq <- decostand(positive.clean.count, method = 'total')

### Exercise 8.2 – Compute entropy and diversity spectra

Apply `H_spectrum()` and `D_spectrum()` to every cleaned PCR (using the same `qs`) and summarize the distributions (e.g., via `rowMeans` or boxplots).

In [ ]:
# your work here

In [ ]:
# Solution
positive.clean.H <- apply(positive.clean.count.relfreq, MARGIN = 1, H_spectrum, q = qs)
positive.clean.D <- apply(positive.clean.count.relfreq, MARGIN = 1, D_spectrum, q = qs)
positive.clean.H.means <- rowMeans(positive.clean.H)
positive.clean.D.means <- rowMeans(positive.clean.D)
list(H = positive.clean.H, D = positive.clean.D,
     H.means = positive.clean.H.means,
     D.means = positive.clean.D.means)

## Series 9 – β-diversity: Guiana rainforest case study
Focus: cleaning replicated PCRs, averaging them, and building several distance matrices on the Guiana dataset exactly like on the slides.

### Exercise 9.1 – Load Guiana data and flag bad PCRs

Load `guiana.count`, `guiana.samples`, and `guiana.motus`. Then repeat the `tag_bad_pcr()` filtering three times so that only reliable PCRs remain in `guiana.count.clean` and `guiana.samples.clean`.

In [ ]:
# your work here

In [ ]:
# Solution
data('guiana.count')
data('guiana.samples')
data('guiana.motus')
guiana.count.clean <- guiana.count
guiana.samples.clean <- guiana.samples
for (cycle in 1:3) {
  s <- tag_bad_pcr(guiana.samples.clean$sample, guiana.count.clean)
  guiana.count.clean <- guiana.count.clean[s$keep, ]
  guiana.samples.clean <- guiana.samples.clean[s$keep, ]
}
table(s$keep)

### Exercise 9.2 – Average PCR replicates and retain real samples

Bind the `tag_bad_pcr` summary to `guiana.samples.clean`, average counts by biological sample, keep one metadata line per sample, and drop rows without a site identifier.

In [ ]:
# your work here

In [ ]:
# Solution
guiana.samples.clean <- cbind(guiana.samples.clean, s[rownames(guiana.samples.clean), ])
guiana.count.mean <- aggregate(decostand(guiana.count.clean, method = 'total'),
                              by = list(guiana.samples.clean$sample), FUN = mean)
rownames(guiana.count.mean) <- guiana.count.mean[, 1]
guiana.count.mean <- as.matrix(guiana.count.mean[, -1])
guiana.samples.mean <- aggregate(guiana.samples.clean,
                                by = list(guiana.samples.clean$sample),
                                FUN = function(i) i[1])
rownames(guiana.samples.mean) <- guiana.samples.mean[, 1]
guiana.samples.mean <- guiana.samples.mean[, -1]
guiana.samples.final <- guiana.samples.mean[!is.na(guiana.samples.mean$site_id), ]
guiana.count.final <- guiana.count.mean[rownames(guiana.samples.final), ]

### Exercise 9.3 – Create transformed matrices

Compute the Hellinger transformation, relative frequencies, and presence/absence thresholds (0.1%, 1%, and 5%) used later in the slides.

In [ ]:
# your work here

In [ ]:
# Solution
guiana.hellinger.final <- decostand(guiana.count.final, method = 'hellinger')
guiana.relfreq.final <- decostand(guiana.count.final, method = 'total')
guiana.presence.1.final <- guiana.relfreq.final > 0.001
guiana.presence.10.final <- guiana.relfreq.final > 0.01
guiana.presence.50.final <- guiana.relfreq.final > 0.05

### Exercise 9.4 – Compute distance matrices

Using `vegdist()`, reproduce the Bray–Curtis, Euclidean (on Hellinger), and Jaccard (three thresholds) distances.

In [ ]:
# your work here

In [ ]:
# Solution
guiana.bc.dist <- vegdist(guiana.relfreq.final, method = 'bray')
guiana.euc.dist <- vegdist(guiana.hellinger.final, method = 'euclidean')
guiana.jac.1.dist <- vegdist(guiana.presence.1.final, method = 'jaccard')
guiana.jac.10.dist <- vegdist(guiana.presence.10.final, method = 'jaccard')
guiana.jac.50.dist <- vegdist(guiana.presence.50.final, method = 'jaccard')

## Series 10 – Ordination and diversity comparisons
Focus: recreating the ordination figures and the final comparison of α-diversity spectra across sites/materials.

### Exercise 10.1 – Run principal coordinate analyses

Apply `cmdscale()` (with `k = 3`) to every distance matrix and store the resulting objects for plotting.

In [ ]:
# your work here

In [ ]:
# Solution
guiana.bc.pcoa <- cmdscale(guiana.bc.dist, k = 3, eig = TRUE)
guiana.euc.pcoa <- cmdscale(guiana.euc.dist, k = 3, eig = TRUE)
guiana.jac.1.pcoa <- cmdscale(guiana.jac.1.dist, k = 3, eig = TRUE)
guiana.jac.10.pcoa <- cmdscale(guiana.jac.10.dist, k = 3, eig = TRUE)
guiana.jac.50.pcoa <- cmdscale(guiana.jac.50.dist, k = 3, eig = TRUE)

### Exercise 10.2 – Compare Euclidean PCoA and PCA

Create the `samples.type` factor (Material × Site), plot the Euclidean PCoA (first two axes), and run a PCA on the Hellinger-transformed data to mirror the lecture.

In [ ]:
# your work here

In [ ]:
# Solution
samples.type <- interaction(guiana.samples.final$Material,
                                 guiana.samples.final$Site, drop = FALSE)
par(mfrow = c(1, 2), bg = NA)
plot(guiana.euc.pcoa$points[, 1:2], col = samples.type, asp = 1,
     xlab = 'Axis 1', ylab = 'Axis 2', main = 'Euclidean on Hellinger')
guiana.hellinger.pca <- prcomp(guiana.hellinger.final, center = TRUE, scale. = FALSE)
plot(guiana.hellinger.pca$x[, 1:2], col = samples.type, asp = 1,
     xlab = 'Axis 1', ylab = 'Axis 2', main = 'PCA on Hellinger data')

### Exercise 10.3 – Compare diversity spectra by habitat

Apply `H_spectrum()` to each averaged Guiana sample (using the same `qs`) and reproduce the boxplots comparing Mana vs Petit Plateau and Litter vs Soil.

In [ ]:
# your work here

In [ ]:
# Solution
guiana.relfreq.spectra <- apply(guiana.relfreq.final, MARGIN = 1, H_spectrum, q = qs)
par(mfrow = c(2, 2), bg = NA)
boxplot(t(guiana.relfreq.spectra[, samples.type == 'litter.Mana']), log = 'y',
        names = qs, las = 2, main = 'Mana litter', ylab = expression(''^q * H))
boxplot(t(guiana.relfreq.spectra[, samples.type == 'soil.Mana']), log = 'y',
        names = qs, las = 2, main = 'Mana soil', ylab = expression(''^q * H))
boxplot(t(guiana.relfreq.spectra[, samples.type == 'litter.Petit Plateau']), log = 'y',
        names = qs, las = 2, main = 'Petit Plateau litter', ylab = expression(''^q * H))
boxplot(t(guiana.relfreq.spectra[, samples.type == 'soil.Petit Plateau']), log = 'y',
        names = qs, las = 2, main = 'Petit Plateau soil', ylab = expression(''^q * H))